<a href="https://colab.research.google.com/github/SarthakShah001/Tweets-Classifier/blob/main/GraphMining.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
from google.colab import drive
drive.mount('/content/gdrive')

Drive already mounted at /content/gdrive; to attempt to forcibly remount, call drive.mount("/content/gdrive", force_remount=True).


In [ ]:
!pip install emoji

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
from emoji import demojize
from nltk.tokenize import TweetTokenizer
tokenizer = TweetTokenizer()


def normalizeToken(token):
    lowercased_token = token.lower()
    if token.startswith("@"):
        return "@USER"
    elif lowercased_token.startswith("http") or lowercased_token.startswith("www"):
        return "HTTPURL"
    elif len(token) == 1:
        return demojize(token)
    else:
        if token == "’":
            return "'"
        elif token == "…":
            return "..."
        else:
            return token

def normalizeTweet(tweet):
    tokens = tokenizer.tokenize(tweet.replace("’", "'").replace("…", "..."))
    normTweet = " ".join([normalizeToken(token) for token in tokens])

    normTweet = (
        normTweet.replace("cannot ", "can not ")
        .replace("n't ", " n't ")
        .replace("n 't ", " n't ")
        .replace("ca n't", "can't")
        .replace("ai n't", "ain't")
    )
    normTweet = (
        normTweet.replace("'m ", " 'm ")
        .replace("'re ", " 're ")
        .replace("'s ", " 's ")
        .replace("'ll ", " 'll ")
        .replace("'d ", " 'd ")
        .replace("'ve ", " 've ")
    )
    normTweet = (
        normTweet.replace(" p . m .", "  p.m.")
        .replace(" p . m ", " p.m ")
        .replace(" a . m .", " a.m.")
        .replace(" a . m ", " a.m ")
    )

    return " ".join(normTweet.split())

In [ ]:
import numpy as np
import pickle as pkl
import networkx as nx
import scipy.sparse as sp
from scipy.sparse.linalg.eigen.arpack import eigsh
import sys
import re

def loadWord2Vec(filename):
    """Read Word Vectors"""
    vocab = []
    embd = []
    word_vector_map = {}
    file = open(filename, 'r')
    for line in file.readlines():
        row = line.strip().split(' ')
        if(len(row) > 2):
            vocab.append(row[0])
            vector = row[1:]
            length = len(vector)
            for i in range(length):
                vector[i] = float(vector[i])
            embd.append(vector)
            word_vector_map[row[0]] = vector
    print('Loaded Word Vectors!')
    file.close()
    return vocab, embd, word_vector_map

def clean_str(string):
    string = re.sub(r"[^A-Za-z0-9(),!?\'\`]", " ", string)
    string = re.sub(r"\'s", " \'s", string)
    string = re.sub(r"\'ve", " \'ve", string)
    string = re.sub(r"n\'t", " n\'t", string)
    string = re.sub(r"\'re", " \'re", string)
    string = re.sub(r"\'d", " \'d", string)
    string = re.sub(r"\'ll", " \'ll", string)
    string = re.sub(r",", " , ", string)
    string = re.sub(r"!", " ! ", string)
    string = re.sub(r"\(", " \( ", string)
    string = re.sub(r"\)", " \) ", string)
    string = re.sub(r"\?", " \? ", string)
    string = re.sub(r"\s{2,}", " ", string)
    return string.strip().lower()

In [ ]:
import csv
from csv import reader
# open file in read mode
file1 = open("myfile.txt","w")



with open('/content/gdrive/MyDrive/Graph Mining/data/tweet_data/train.csv', 'r') as read_obj:
    # pass the file object to reader() to get the reader object
    csv_reader = reader(read_obj)
    # Iterate over each row in the csv using reader object
    for row in csv_reader:
        # row variable is a list that represents a row in csv
        s=''.join([str(elem)for elem in row])
        
        #    csvwriter = csv.writer(csvfile) 
        
        #  # writing the fields 
        #    a=normalizeTweet(s)
        #    csvwriter.writerow(a) 
        #    print(a)
        s+=('\n')
        file1.writelines(s)
file1.close()

In [ ]:
tweets=[]
meta_data_list = []

dataset_name = 'myfile'

f = open('' + dataset_name + '.txt', 'r')
lines = f.readlines()
for line in lines:
    temp = line.split("\t")
    meta = temp[0] + '\t' + 'train' + '\t' + temp[2]+'\t'+temp[3]+'\t'+temp[4] +'\t' +temp[5]
    # print(meta)
    meta_data_list.append(meta)
    tweets.append(temp[1])
f.close()
dataset_name = '2018'
meta_data_str = ''.join(meta_data_list)
print(meta_data_str)
f = open('data/' + dataset_name + '.txt', 'w')
f.write(meta_data_str)
f.close()
print(tweets)
corpus_str = '\n'.join(tweets)
print(corpus_str)
f = open('data/corpus/' + dataset_name + '.txt', 'w')
f.write(corpus_str)
f.close()

ID	train	joy	sadness	anger	fear
2017-En-10000	train	0.0	0.0	0.938	0.0
2017-En-10001	train	0.0	0.0	0.8959999999999999	0.0
2017-En-10002	train	0.0	0.0	0.8959999999999999	0.0
2017-En-10003	train	0.0	0.0	0.8959999999999999	0.0
2017-En-10004	train	0.0	0.0	0.8959999999999999	0.0
2017-En-10005	train	0.0	0.0	0.875	0.0
2017-En-10006	train	0.0	0.0	0.875	0.0
2017-En-10007	train	0.0	0.0	0.875	0.0
2017-En-10008	train	0.0	0.0	0.875	0.0
2017-En-10009	train	0.0	0.0	0.875	0.0
2017-En-10010	train	0.0	0.0	0.667	0.0
2017-En-10011	train	0.0	0.0	0.8540000000000001	0.0
2017-En-10012	train	0.0	0.0	0.8540000000000001	0.0
2017-En-10013	train	0.0	0.0	0.938	0.0
2017-En-10014	train	0.0	0.0	0.8540000000000001	0.0
2017-En-10015	train	0.0	0.0	0.8540000000000001	0.0
2017-En-10016	train	0.0	0.0	0.8540000000000001	0.0
2017-En-10017	train	0.0	0.0	0.833	0.0
2017-En-10018	train	0.0	0.0	0.833	0.0
2017-En-10019	train	0.0	0.0	0.812	0.0
2017-En-10020	train	0.0	0.0	0.812	0.0
2017-En-10021	train	0.0	0.0	0.8909999999999999	0.0
20

In [ ]:
from nltk.corpus import stopwords
import nltk
from nltk.wsd import lesk
nltk.download('wordnet')
import sys

dataset = '2018'

nltk.download('stopwords')
stop_words = set(stopwords.words('english'))
print(stop_words)

doc_content_list = []
f = open('data/corpus/' + dataset + '.txt', 'rb')
# f = open('data/wiki_long_abstracts_en_text.txt', 'r')
for line in f.readlines():
    doc_content_list.append(line.strip().decode('latin1'))
f.close()


word_freq = {}  # to remove rare words

for doc_content in doc_content_list:
    temp = clean_str(doc_content)
    words = temp.split()
    for word in words:
        if word in word_freq:
            word_freq[word] += 1
        else:
            word_freq[word] = 1

clean_docs = []
for doc_content in doc_content_list:
    temp = clean_str(doc_content)
    words = temp.split()
    doc_words = []
    for word in words:
        # word not in stop_words and word_freq[word] >= 5
        if dataset == 'mr':
            doc_words.append(word)
        elif word not in stop_words and word_freq[word] >= 5:
            doc_words.append(word)

    doc_str = ' '.join(doc_words).strip()
    #if doc_str == '':
        #doc_str = temp
    clean_docs.append(doc_str)

clean_corpus_str = '\n'.join(clean_docs)

f = open('data/corpus/' + dataset + '.clean.txt', 'w')
#f = open('data/wiki_long_abstracts_en_text.clean.txt', 'w')
f.write(clean_corpus_str)
f.close()

#dataset = '20ng'
min_len = 10000
aver_len = 0
max_len = 0 

f = open('data/corpus/' + dataset + '.clean.txt', 'r')
#f = open('data/wiki_long_abstracts_en_text.txt', 'r')
lines = f.readlines()
for line in lines:
    line = line.strip()
    temp = line.split()
    aver_len = aver_len + len(temp)
    if len(temp) < min_len:
        min_len = len(temp)
    if len(temp) > max_len:
        max_len = len(temp)
f.close()
aver_len = 1.0 * aver_len / len(lines)
print('min_len : ' + str(min_len))
print('max_len : ' + str(max_len))
print('average_len : ' + str(aver_len))

[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.


{'an', 'through', 'you', 'doing', 'off', "that'll", 'being', 'does', 'was', 'will', 'not', 'or', 're', 'most', 'if', 'there', 'with', 'such', 'very', 'below', "hadn't", "shouldn't", 'isn', "won't", "mustn't", 'out', 'himself', 'we', 'when', 'which', 'been', 'wouldn', 'on', 'herself', 'do', 'our', 'can', "she's", 'theirs', 'so', 'these', 'couldn', 'for', 'more', "hasn't", 'where', "you're", 'yourself', "shan't", 'some', 'after', 'themselves', 'other', 'nor', 'am', 'them', "isn't", "needn't", 'now', "aren't", 'what', 'into', 'because', 'haven', 'has', 'wasn', 'yours', 'to', 'm', 'once', 'only', 'yourselves', 'both', 've', 'had', 'shan', 'him', 'doesn', 'no', 'your', 'did', 'of', 'further', 'but', 'aren', 'myself', 'about', 'ma', 'her', 'they', 'at', 'just', 'she', 'than', "you'll", 'each', 'mightn', "didn't", 'weren', 'y', 'he', 'itself', 'how', 'this', 'didn', "wouldn't", 'mustn', 'my', 'against', 'is', 'in', 'all', 'between', 'i', 'ours', 'while', 'it', 'its', 'over', "weren't", "don't

In [ ]:
print(clean_corpus_str)

tweet
k ! ! moved ! door angry mad
indian uber driver called someone n word n't moving 'd disgusted
uk asked delivered pick store address fuming
fire alarm bc sound asleep pissed angry upset tired sad tired hangry
n't join put phone talk rude taking money ! fuming
blood boiling
've still got whole season watch stupid cunt work us raging
bt uk tracking show delivered n't \? service suddenly \? 've already 3 weeks fuming
legit furious people fucking
suppose work \? wtf dude \? thanks
im mad power im im furious
use using ! ! guys cant get nothing right ! ! fuming
aggravate like biggest cunt known man kind \?
come night working fucking gutted waiting appearance ages raging
fuming
zero help customer service pushing back happen anger
mention guy let 's 2 ppl front go wtf blood boiling
hate soul 'd fiery hell
people offended photo shoot like seriously shut fuck
i'm block everyone everywhere storm think everyone damn rain quit damn
making cry ! ! bitch wait revenge
! n't tell true switch f c t

In [ ]:
import os
import random
import numpy as np
import pickle as pkl
import networkx as nx
import scipy.sparse as sp
from math import log
from sklearn import svm
from nltk.corpus import wordnet as wn
from sklearn.feature_extraction.text import TfidfVectorizer
import sys
from scipy.spatial.distance import cosine

In [ ]:
# build corpus
dataset = '2018'

word_embeddings_dim = 300
word_vector_map = {}

# shulffing
doc_name_list = []
doc_train_list = []

f = open('data/' + dataset + '.txt', 'r')
lines = f.readlines()
for line in lines:
    doc_name_list.append(line.strip())
    temp = line.split("\t")
    print(temp)
    if temp[1].find('train') != -1:
        doc_train_list.append(line.strip())
f.close()
print(doc_train_list)

In [ ]:
doc_content_list = []
f = open('data/corpus/' + dataset + '.clean.txt', 'r')
lines = f.readlines()
for line in lines:
    doc_content_list.append(line.strip())
f.close()
print(doc_content_list)

['tweet', 'k ! ! moved ! door angry mad', "indian uber driver called someone n word n't moving 'd disgusted", 'uk asked delivered pick store address fuming', 'fire alarm bc sound asleep pissed angry upset tired sad tired hangry', "n't join put phone talk rude taking money ! fuming", 'blood boiling', "'ve still got whole season watch stupid cunt work us raging", "bt uk tracking show delivered n't \\? service suddenly \\? 've already 3 weeks fuming", 'legit furious people fucking', 'suppose work \\? wtf dude \\? thanks', 'im mad power im im furious', 'use using ! ! guys cant get nothing right ! ! fuming', 'aggravate like biggest cunt known man kind \\?', 'come night working fucking gutted waiting appearance ages raging', 'fuming', 'zero help customer service pushing back happen anger', "mention guy let 's 2 ppl front go wtf blood boiling", "hate soul 'd fiery hell", 'people offended photo shoot like seriously shut fuck', "i'm block everyone everywhere storm think everyone damn rain quit 

In [ ]:
train_ids = []
for train_name in doc_train_list:
    train_id = doc_name_list.index(train_name)
    train_ids.append(train_id)
print(train_ids)
random.shuffle(train_ids)

# partial labeled data
#train_ids = train_ids[:int(0.2 * len(train_ids))]

train_ids_str = '\n'.join(str(index) for index in train_ids)
f = open('data/' + dataset + '.train.index', 'w')
f.write(train_ids_str)
f.close()

[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, 100, 101, 102, 103, 104, 105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 142, 143, 144, 145, 146, 147, 148, 149, 150, 151, 152, 153, 154, 155, 156, 157, 158, 159, 160, 161, 162, 163, 164, 165, 166, 167, 168, 169, 170, 171, 172, 173, 174, 175, 176, 177, 178, 179, 180, 181, 182, 183, 184, 185, 186, 187, 188, 189, 190, 191, 192, 193, 194, 195, 196, 197, 198, 199, 200, 201, 202, 203, 204, 205, 206, 207, 208, 209, 210, 211, 212, 213, 214, 215, 216, 217, 218, 219, 220, 221,

In [ ]:
ids = train_ids
print(ids)
print(len(ids))

[1595, 1554, 4507, 1660, 4557, 2539, 6728, 4292, 4684, 4851, 6003, 5001, 5548, 3300, 113, 2221, 2583, 403, 525, 2095, 984, 6152, 1979, 287, 443, 4014, 5326, 5137, 6250, 2985, 6468, 1626, 3702, 4372, 3894, 2633, 3798, 3578, 2199, 3382, 1996, 2161, 1579, 2177, 417, 2722, 1160, 1263, 4211, 5544, 4199, 1312, 4258, 2403, 1596, 411, 1278, 4290, 3669, 2096, 3759, 4485, 1693, 526, 5622, 6592, 1890, 4047, 2292, 2381, 6252, 2975, 3438, 2301, 217, 1969, 5517, 1633, 3769, 4576, 1226, 946, 6622, 6634, 1146, 6542, 4371, 4765, 2580, 1761, 3385, 2894, 877, 2419, 571, 5129, 4108, 6135, 6342, 1489, 3281, 1549, 6527, 1065, 4228, 5749, 3171, 5898, 4580, 686, 6449, 1444, 1799, 3004, 2498, 4496, 1313, 1273, 1035, 2953, 6798, 5005, 6591, 356, 3854, 1352, 1107, 2846, 2990, 6726, 3334, 5182, 4663, 6718, 3962, 5020, 6022, 6195, 5705, 4975, 2317, 577, 1274, 2042, 4836, 3566, 2174, 3079, 6368, 1497, 524, 1916, 5071, 1738, 6635, 5259, 846, 4166, 5603, 4013, 2182, 4709, 2866, 4245, 1903, 5738, 6761, 6127, 3647, 881

In [ ]:
orglabel_list=[]
for doc_meta in doc_name_list:
    temp = doc_meta.split('\t')
    orglabel_list.append(temp[2:6])


label_list_str = '\n'.join(str(elem) for elem in orglabel_list)
f = open('data/corpus/' + dataset + '_labels.txt', 'w')
f.write(label_list_str)
f.close()
print(orglabel_list)

[['joy', 'sadness', 'anger', 'fear'], ['0.0', '0.0', '0.938', '0.0'], ['0.0', '0.0', '0.8959999999999999', '0.0'], ['0.0', '0.0', '0.8959999999999999', '0.0'], ['0.0', '0.0', '0.8959999999999999', '0.0'], ['0.0', '0.0', '0.8959999999999999', '0.0'], ['0.0', '0.0', '0.875', '0.0'], ['0.0', '0.0', '0.875', '0.0'], ['0.0', '0.0', '0.875', '0.0'], ['0.0', '0.0', '0.875', '0.0'], ['0.0', '0.0', '0.875', '0.0'], ['0.0', '0.0', '0.667', '0.0'], ['0.0', '0.0', '0.8540000000000001', '0.0'], ['0.0', '0.0', '0.8540000000000001', '0.0'], ['0.0', '0.0', '0.938', '0.0'], ['0.0', '0.0', '0.8540000000000001', '0.0'], ['0.0', '0.0', '0.8540000000000001', '0.0'], ['0.0', '0.0', '0.8540000000000001', '0.0'], ['0.0', '0.0', '0.833', '0.0'], ['0.0', '0.0', '0.833', '0.0'], ['0.0', '0.0', '0.812', '0.0'], ['0.0', '0.0', '0.812', '0.0'], ['0.0', '0.0', '0.8909999999999999', '0.0'], ['0.0', '0.0', '0.812', '0.0'], ['0.0', '0.0', '0.812', '0.0'], ['0.0', '0.0', '0.792', '0.0'], ['0.0', '0.0', '0.792', '0.0'], 

In [ ]:
shuffle_doc_name_list = []
shuffle_doc_words_list = []
for id in ids:
    shuffle_doc_name_list.append(doc_name_list[int(id)])
    shuffle_doc_words_list.append(doc_content_list[int(id)])
shuffle_doc_name_str = '\n'.join(shuffle_doc_name_list)
shuffle_doc_words_str = '\n'.join(shuffle_doc_words_list)

f = open('data/' + dataset + '_shuffle.txt', 'w')
f.write(shuffle_doc_name_str)
f.close()

f = open('data/corpus/' + dataset + '_shuffle.txt', 'w')
f.write(shuffle_doc_words_str)
f.close()
print(shuffle_doc_name_list)
print(shuffle_doc_words_list)

['2017-En-11684\ttrain\t0.0\t0.0\t0.667\t0.0', '2017-En-11642\ttrain\t0.0\t0.0\t0.5\t0.0', '2017-En-30645\ttrain\t0.32\t0.0\t0.0\t0.0', '2017-En-20049\ttrain\t0.0\t0.0\t0.0\t0.8540000000000001', '2017-En-30695\ttrain\t0.271\t0.0\t0.0\t0.0', '2017-En-20928\ttrain\t0.0\t0.0\t0.0\t0.312', '2017-En-41337\ttrain\t0.0\t0.292\t0.0\t0.0', '2017-En-30429\ttrain\t0.48\t0.0\t0.0\t0.0', '2017-En-30823\ttrain\t0.312\t0.0\t0.0\t0.0', '2017-En-30990\ttrain\t0.22899999999999998\t0.0\t0.0\t0.0', '2017-En-40567\ttrain\t0.0\t0.354\t0.0\t0.0', '2017-En-31140\ttrain\t0.688\t0.0\t0.0\t0.0', '2017-En-40077\ttrain\t0.0\t0.75\t0.0\t0.0', '2017-En-21689\ttrain\t0.0\t0.0\t0.0\t0.562', '2017-En-10112\ttrain\t0.0\t0.0\t0.708\t0.0', '2017-En-20610\ttrain\t0.0\t0.0\t0.0\t0.46', '2017-En-20972\ttrain\t0.0\t0.0\t0.0\t0.292', '2017-En-10421\ttrain\t0.0\t0.0\t0.494\t0.0', '2017-En-10546\ttrain\t0.0\t0.0\t0.491\t0.0', '2017-En-20484\ttrain\t0.0\t0.0\t0.0\t0.521', '2017-En-11045\ttrain\t0.0\t0.0\t0.312\t0.0', '2017-En-407

In [ ]:
# build vocab
word_freq = {}
word_set = set()
for doc_words in shuffle_doc_words_list:
    words = doc_words.split()
    for word in words:
        word_set.add(word)
        if word in word_freq:
            word_freq[word] += 1
        else:
            word_freq[word] = 1

vocab = list(word_set)
vocab_size = len(vocab)
print(vocab)

['brexit', 'whilst', 'atlanta', 'network', 'wwe', 'lead', 'govt', 'say', 'people', 'move', 'comments', 'upon', 'charge', 'kurt', 'supporting', 'data', 'oh', 'ruin', 'channel', 'brought', 'open', 'given', 'michelle', 'writing', 'whenever', 'cops', 'delete', 'died', 'crap', 'paul', 'turns', 'opinion', 'spry', 'em', 'complete', 'worrying', 'street', 'prayer', 'nso', 'little', 'rip', 'stressed', 'clock', 'something', 'experience', 'etc', 'saturday', 'blocks', 'family', 'earlier', 'doubt', 'successful', 'change', 'hahaha', 'projection', 'russia', 'amwriting', 'incredible', 'lovely', 'rn', 'decide', 'friday', 'goes', 'face', 'keeps', 'writers', 'machine', 'research', 'join', 'harry', 'refugees', 'free', 'pay', 'ordered', 'space', 'tears', 'luck', 'chronic', 'way', '90', 'great', 'doctor', 'wasted', 'nfl', 'racism', 'depressed', 'leadership', 'brave', 'uncle', 'sent', 'peoplelikemebecause', 'fallen', 'pissed', 'depressing', 'much', 'live', 'sis', 'destroyed', 'bitter', 'wifi', 'throw', 'terri

In [ ]:
word_doc_list = {}

for i in range(len(shuffle_doc_words_list)):
    doc_words = shuffle_doc_words_list[i]
    words = doc_words.split()
    appeared = set()
    for word in words:
        if word in appeared:
            continue
        if word in word_doc_list:
            doc_list = word_doc_list[word]
            doc_list.append(i)
            word_doc_list[word] = doc_list
        else:
            word_doc_list[word] = [i]
        appeared.add(word)
print(word_doc_list)

{'allowed': [0, 85, 1168, 2494, 4754, 5982], 'start': [0, 71, 329, 446, 510, 573, 618, 656, 695, 857, 915, 969, 1132, 1163, 1205, 1289, 1403, 1441, 1523, 1528, 1547, 1605, 1615, 1830, 1841, 1994, 2082, 2128, 2178, 2269, 2348, 2390, 2551, 2596, 2605, 2748, 2782, 2808, 2973, 3182, 3200, 3289, 3293, 3298, 3391, 3550, 3653, 3736, 3745, 3769, 3791, 3940, 4176, 4188, 4247, 4261, 4315, 4369, 4400, 4412, 4413, 4445, 4490, 4577, 4603, 4616, 4667, 4675, 4790, 4822, 4857, 4909, 5084, 5129, 5135, 5208, 5259, 5318, 5448, 5548, 5695, 5746, 5770, 5778, 5792, 5972, 5974, 6047, 6081, 6108, 6219, 6245, 6318, 6350, 6394, 6475, 6536, 6580, 6755, 6837, 6854, 6896], 'taking': [0, 55, 356, 392, 774, 826, 922, 1202, 1205, 2068, 2255, 2760, 2799, 3603, 4060, 4063, 4158, 4222, 4365, 4394, 4775, 4891, 5208, 5367, 5515, 5646, 5836, 6149, 6400, 6499], 'set': [0, 431, 1046, 1163, 1176, 1302, 2030, 2398, 3009, 3560, 3568, 3819, 4044, 4866, 5021, 5023, 5089, 5185, 5253], '\\?': [0, 16, 17, 31, 52, 61, 62, 65, 89, 90,

In [ ]:
word_doc_freq = {}
total_len=0
for word, doc_list in word_doc_list.items():
    word_doc_freq[word] = len(doc_list)
    total_len+=word_doc_freq[word]
word_id_map = {}
for i in range(vocab_size):
    word_id_map[vocab[i]] = i

vocab_str = '\n'.join(vocab)

f = open('data/corpus/' + dataset + '_vocab.txt', 'w')
f.write(vocab_str)
f.close()
print(word_doc_freq)
print(total_len)

{'allowed': 6, 'start': 102, 'taking': 30, 'set': 19, '\\?': 654, 'fuming': 69, 'every': 86, 'day': 209, 'think': 172, 'house': 42, 'burning': 45, "'s": 938, 'always': 136, '!': 1054, 'lively': 61, 'well': 87, 'mad': 29, 'quick': 8, 'white': 41, 'americans': 12, 'worried': 16, 'black': 55, 'fearful': 7, 'terrorist': 14, 'police': 37, 'daily': 6, 'also': 63, 'called': 25, 'halloween': 10, 'party': 20, 'coming': 24, 'soon': 32, 'lit': 9, 'scary': 16, 'haunt': 19, 'times': 35, 'better': 78, 'guitar': 5, 'music': 38, 'blues': 76, 'jaunty': 9, 'watching': 55, 'late': 31, 'lol': 113, 'thought': 56, 'maybe': 48, 'could': 114, "n't": 840, 'decide': 12, 'levity': 26, 'may': 49, 'right': 110, 'since': 55, 'year': 54, 'bad': 88, 'begin': 9, 'b': 27, "i'm": 459, 'hoping': 12, "'ve": 164, 'got': 158, 'least': 37, 'c': 14, 'z': 6, 'go': 166, '1st': 11, 'know': 223, 'man': 100, 'assume': 9, 'realdonaldtrump': 31, 'argument': 5, 'great': 83, 'see': 164, 'happy': 195, 'new': 130, 'chair': 7, 'access': 

In [ ]:
# label list
label_list=[]
for doc_meta in shuffle_doc_name_list:
    temp = doc_meta.split('\t')
    label_list.append(temp[2:6])


label_list_str = '\n'.join(str(elem) for elem in label_list)
f = open('data/corpus/' + dataset + '_labels.txt', 'w')
f.write(label_list_str)
f.close()
print(label_list)

[['0.0', '0.0', '0.667', '0.0'], ['0.0', '0.0', '0.5', '0.0'], ['0.32', '0.0', '0.0', '0.0'], ['0.0', '0.0', '0.0', '0.8540000000000001'], ['0.271', '0.0', '0.0', '0.0'], ['0.0', '0.0', '0.0', '0.312'], ['0.0', '0.292', '0.0', '0.0'], ['0.48', '0.0', '0.0', '0.0'], ['0.312', '0.0', '0.0', '0.0'], ['0.22899999999999998', '0.0', '0.0', '0.0'], ['0.0', '0.354', '0.0', '0.0'], ['0.688', '0.0', '0.0', '0.0'], ['0.0', '0.75', '0.0', '0.0'], ['0.0', '0.0', '0.0', '0.562'], ['0.0', '0.0', '0.708', '0.0'], ['0.0', '0.0', '0.0', '0.46'], ['0.0', '0.0', '0.0', '0.292'], ['0.0', '0.0', '0.494', '0.0'], ['0.0', '0.0', '0.491', '0.0'], ['0.0', '0.0', '0.0', '0.521'], ['0.0', '0.0', '0.312', '0.0'], ['0.0', '0.235', '0.0', '0.0'], ['0.0', '0.0', '0.0', '0.583'], ['0.0', '0.0', '0.562', '0.0'], ['0.0', '0.0', '0.479', '0.0'], ['0.688', '0.0', '0.0', '0.0'], ['0.708', '0.0', '0.0', '0.0'], ['0.82', '0.0', '0.0', '0.0'], ['0.0', '0.44', '0.0', '0.0'], ['0.0', '0.0', '0.0', '0.542'], ['0.0', '0.332999999

In [ ]:
# x: feature vectors of training docs, no initial features
# slect 90% training set
train_size = len(train_ids)
val_size = int(0.1 * train_size)
real_train_size = train_size - val_size  # - int(0.5 * train_size)
# different training rates

real_train_doc_names = shuffle_doc_name_list[:real_train_size]
real_train_doc_names_str = '\n'.join(real_train_doc_names)

f = open('data/' + dataset + '.real_train.name', 'w')
f.write(real_train_doc_names_str)
f.close()
print(len(real_train_doc_names))

6219


In [ ]:
nltk.download('omw-1.4')

[nltk_data] Downloading package omw-1.4 to /root/nltk_data...


True

In [ ]:
definitions = []
for word in vocab:
    word = word.strip()
    synsets = wn.synsets(clean_str(word))
    word_defs = []
    for synset in synsets:
        syn_def = synset.definition()
        word_defs.append(syn_def)
    word_des = ' '.join(word_defs)
    if word_des == '':
        word_des = '<PAD>'
    definitions.append(word_des)
string = '\n'.join(definitions)
f = open('data/corpus/' + dataset + '_vocab_def.txt', 'w')
f.write(string)
f.close()
tfidf_vec = TfidfVectorizer(max_features=1000)
tfidf_matrix = tfidf_vec.fit_transform(definitions)
tfidf_matrix_array = tfidf_matrix.toarray()
print(tfidf_matrix_array[0], len(tfidf_matrix_array[0]))
word_vectors = []
for i in range(len(vocab)):
    word = vocab[i]
    vector = tfidf_matrix_array[i]
    str_vector = []
    for j in range(len(vector)):
        str_vector.append(str(vector[j]))
    temp = ' '.join(str_vector)
    word_vector = word + ' ' + temp
    word_vectors.append(word_vector)
string = '\n'.join(word_vectors)
f = open('data/corpus/' + dataset + '_word_vectors.txt', 'w')
f.write(string)
f.close()
word_vector_file = 'data/corpus/' + dataset + '_word_vectors.txt'
_, embd, word_vector_map = loadWord2Vec(word_vector_file)
word_embeddings_dim = len(embd[0])

[0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.

In [ ]:
print(shuffle_doc_words_list)

['allowed start taking set \\? fuming', "every day think house burning 's always burning !", 'lively well mad quick', 'white americans worried black americans fearful terrorist police daily', 'also called', 'halloween party coming soon ! lit scary haunt', "'s times better 's guitar music blues", 'jaunty watching late !', "lol thought maybe could n't decide levity", "may right since year bad begin b i'm hoping 've got least c z go 1st", 'know man assume realdonaldtrump argument', "'s great see happy new chair access lots new experiences", "horrid ! affliction 's hard", 'book like holy crap', "i'm fuming ball anger today", 'horror top close cup good think pressure get mark', 'good horror every year old shit \\?', 'date \\? \\? \\? \\? \\? offended', 'go kid outrage means mean', '20 says gets afraid', "favourite quote year far 'i", "ass lil boys yeah ca n't take serious", 'car crash st traffic horrid', 'let id fuming poor keeping', "blog says simon 'll expect", 'us early thy mercy may rej

In [ ]:
print(word_vector_map['fear'])

[0.0, 0.0, 0.21813521926358576, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.1677260581257027, 0.051635505365695084, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.41250224375357025, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.058009212875380495, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0

In [ ]:
row_x = []
col_x = []
data_x = []
for i in range(real_train_size):
    doc_vec = np.array([0.0 for k in range(word_embeddings_dim)])
    doc_words = shuffle_doc_words_list[i]
    words = doc_words.split()
    doc_len = len(words)
    for word in words:
        if word in word_vector_map:
            word_vector = word_vector_map[word]
            # print(doc_vec)
            # print(np.array(word_vector))
            doc_vec = doc_vec + np.array(word_vector)
    for j in range(word_embeddings_dim):
        row_x.append(i)
        col_x.append(j)
        # np.random.uniform(-0.25, 0.25)
        data_x.append(doc_vec[j] / doc_len)  # doc_vec[j]/ doc_len
print(data_x)


<ipython-input-31-12c0eaad04ce>:19: RuntimeWarning: invalid value encountered in double_scalars
  data_x.append(doc_vec[j] / doc_len)  # doc_vec[j]/ doc_len
IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [ ]:
print(doc_vec.shape)

(1000,)


In [ ]:
# x = sp.csr_matrix((real_train_size, word_embeddings_dim), dtype=np.float32)
x = sp.csr_matrix((data_x, (row_x, col_x)), shape=(
    real_train_size, word_embeddings_dim))

y = []
for i in range(real_train_size):
    doc_meta = shuffle_doc_name_list[i]
    temp = doc_meta.split('\t')
    label = temp[2:6]
    one_hot = [0 for l in range(len(label_list))]
    label_index = label_list.index(label)
    one_hot[label_index] = 1
    y.append(one_hot)
y = np.array(y)
print(y)


[[1 0 0 ... 0 0 0]
 [0 1 0 ... 0 0 0]
 [0 0 1 ... 0 0 0]
 ...
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]]


In [ ]:
# allx: the the feature vectors of both labeled and unlabeled training instances
# (a superset of x)
# unlabeled training instances -> words

word_vectors = np.random.uniform(-0.01, 0.01,
                                 (vocab_size, word_embeddings_dim))

for i in range(len(vocab)):
    word = vocab[i]
    if word in word_vector_map:
        vector = word_vector_map[word]
        word_vectors[i] = vector

row_allx = []
col_allx = []
data_allx = []

for i in range(train_size):
    doc_vec = np.array([0.0 for k in range(word_embeddings_dim)])
    doc_words = shuffle_doc_words_list[i]
    words = doc_words.split()
    doc_len = len(words)
    for word in words:
        if word in word_vector_map:
            word_vector = word_vector_map[word]
            doc_vec = doc_vec + np.array(word_vector)

    for j in range(word_embeddings_dim):
        row_allx.append(int(i))
        col_allx.append(j)
        data_allx.append(doc_vec[j] / doc_len)  
for i in range(vocab_size):
    for j in range(word_embeddings_dim):
        row_allx.append(int(i + train_size))
        col_allx.append(j)
        data_allx.append(word_vectors.item((i, j)))


row_allx = np.array(row_allx)
col_allx = np.array(col_allx)
data_allx = np.array(data_allx)

allx = sp.csr_matrix(
    (data_allx, (row_allx, col_allx)), shape=(train_size + vocab_size, word_embeddings_dim))

ally = []
for i in range(train_size):
    doc_meta = shuffle_doc_name_list[i]
    temp = doc_meta.split('\t')
    label = temp[2:6]
    one_hot = [0 for l in range(len(label_list))]
    label_index = label_list.index(label)
    one_hot[label_index] = 1
    ally.append(one_hot)

for i in range(vocab_size):
    one_hot = [0 for l in range(len(label_list))]
    ally.append(one_hot)

ally = np.array(ally)
print(x.shape, y.shape, allx.shape, ally.shape)

<ipython-input-34-5081d6d6f2cb>:31: RuntimeWarning: invalid value encountered in double_scalars
  data_allx.append(doc_vec[j] / doc_len)


(6219, 1000) (6219, 6909) (9172, 1000) (9172, 6909)


In [ ]:
# word co-occurence with context windows
window_size = 20
windows = []

for doc_words in shuffle_doc_words_list:
    words = doc_words.split()
    length = len(words)
    if length <= window_size:
        windows.append(words)
    else:
        # print(length, length - window_size + 1)
        for j in range(length - window_size + 1):
            window = words[j: j + window_size]
            windows.append(window)
            print(window)

In [ ]:
word_window_freq = {}
for window in windows:
    appeared = set()
    for i in range(len(window)):
        if window[i] in appeared:
            continue
        if window[i] in word_window_freq:
            word_window_freq[window[i]] += 1
        else:
            word_window_freq[window[i]] = 1
        appeared.add(window[i])
print(word_window_freq)

{'allowed': 6, 'start': 102, 'taking': 30, 'set': 19, '\\?': 659, 'fuming': 69, 'every': 86, 'day': 209, 'think': 172, 'house': 42, 'burning': 45, "'s": 938, 'always': 136, '!': 1061, 'lively': 61, 'well': 87, 'mad': 29, 'quick': 8, 'white': 41, 'americans': 12, 'worried': 16, 'black': 55, 'fearful': 7, 'terrorist': 14, 'police': 40, 'daily': 6, 'also': 63, 'called': 25, 'halloween': 10, 'party': 20, 'coming': 24, 'soon': 32, 'lit': 9, 'scary': 16, 'haunt': 19, 'times': 35, 'better': 78, 'guitar': 5, 'music': 39, 'blues': 77, 'jaunty': 9, 'watching': 55, 'late': 34, 'lol': 113, 'thought': 56, 'maybe': 48, 'could': 114, "n't": 842, 'decide': 12, 'levity': 26, 'may': 49, 'right': 110, 'since': 55, 'year': 54, 'bad': 88, 'begin': 9, 'b': 27, "i'm": 460, 'hoping': 12, "'ve": 164, 'got': 164, 'least': 37, 'c': 14, 'z': 6, 'go': 168, '1st': 11, 'know': 224, 'man': 104, 'assume': 9, 'realdonaldtrump': 31, 'argument': 5, 'great': 83, 'see': 164, 'happy': 195, 'new': 130, 'chair': 7, 'access': 

In [ ]:
word_pair_count = {}
for window in windows:
    for i in range(1, len(window)):
        for j in range(0, i):
            word_i = window[i]
            word_i_id = word_id_map[word_i]
            word_j = window[j]
            word_j_id = word_id_map[word_j]
            if word_i_id == word_j_id:
                continue
            word_pair_str = str(word_i_id) + ',' + str(word_j_id)
            if word_pair_str in word_pair_count:
                word_pair_count[word_pair_str] += 1
            else:
                word_pair_count[word_pair_str] = 1
            # two orders
            word_pair_str = str(word_j_id) + ',' + str(word_i_id)
            if word_pair_str in word_pair_count:
                word_pair_count[word_pair_str] += 1
            else:
                word_pair_count[word_pair_str] = 1
# print(word_pair_count)

In [ ]:
row = []
col = []
weight = []

# pmi as weights

num_window = len(windows)

for key in word_pair_count:
    temp = key.split(',')
    i = int(temp[0])
    j = int(temp[1])
    count = word_pair_count[key]
    word_freq_i = word_window_freq[vocab[i]]
    word_freq_j = word_window_freq[vocab[j]]
    pmi = log((1.0 * count / num_window) /
              (1.0 * word_freq_i * word_freq_j/(num_window * num_window)))
    if pmi <= 0:
        continue
    row.append(train_size + i)
    col.append(train_size + j)
    weight.append(pmi)

In [ ]:

# doc word frequency
doc_word_freq = {}

for doc_id in range(len(shuffle_doc_words_list)):
    doc_words = shuffle_doc_words_list[doc_id]
    words = doc_words.split()
    for word in words:
        word_id = word_id_map[word]
        doc_word_str = str(doc_id) + ',' + str(word_id)
        if doc_word_str in doc_word_freq:
            doc_word_freq[doc_word_str] += 1
        else:
            doc_word_freq[doc_word_str] = 1

for i in range(len(shuffle_doc_words_list)):
    doc_words = shuffle_doc_words_list[i]
    words = doc_words.split()
    doc_word_set = set()
    for word in words:
        if word in doc_word_set:
            continue
        j = word_id_map[word]
        key = str(i) + ',' + str(j)
        freq = doc_word_freq[key]
        if i < train_size:
            row.append(i)
        else:
            row.append(i + vocab_size)
        col.append(train_size + j)
        idf = log(1.0 * len(shuffle_doc_words_list) /
                  word_doc_freq[vocab[j]])
        weight.append(freq * idf)
        doc_word_set.add(word)

In [ ]:
node_size = train_size + vocab_size
adj = sp.csr_matrix(
    (weight, (row, col)), shape=(node_size, node_size))
print(adj)

  (0, 7200)	5.439382806826639
  (0, 7959)	5.896141209322354
  (0, 7970)	4.606473683891536
  (0, 8153)	7.04882071926074
  (0, 8218)	2.357472837031596
  (0, 8848)	4.215607375204524
  (1, 7393)	3.6930857116753417
  (1, 7412)	1.9968302394825703
  (1, 7454)	5.1029105702054265
  (1, 7822)	3.498245936523984
  (1, 9092)	10.06783539743695
  (1, 9108)	3.927925302752743
  (1, 9162)	4.386232892235287
  (1, 9163)	1.8802324593874873
  (2, 7269)	4.729706324315484
  (2, 7933)	5.473284358502321
  (2, 8300)	4.374672069834211
  (2, 8591)	6.761138646808959
  (3, 7111)	5.2296622758445706
  (3, 7400)	6.894670039433482
  (3, 7732)	6.067991466249014
  (3, 7734)	7.04882071926074
  (3, 8053)	5.127008121784487
  (3, 8059)	6.2015228588735365
  (3, 8575)	12.711347077401589
  :	:
  (9171, 8869)	2.8186145446350634
  (9171, 8874)	0.6400821003109967
  (9171, 8898)	2.936397580291447
  (9171, 8910)	3.511761725195009
  (9171, 8927)	5.015839121971283
  (9171, 8942)	1.2017965249033404
  (9171, 8947)	1.2781695036879146
  (9

In [ ]:

# dump objects
f = open("data/ind.{}.x".format(dataset), 'wb')
pkl.dump(x, f)
f.close()

f = open("data/ind.{}.y".format(dataset), 'wb')
pkl.dump(y, f)
f.close()

f = open("data/ind.{}.allx".format(dataset), 'wb')
pkl.dump(allx, f)
f.close()

f = open("data/ind.{}.ally".format(dataset), 'wb')
pkl.dump(ally, f)
f.close()

f = open("data/ind.{}.adj".format(dataset), 'wb')
pkl.dump(adj, f)
f.close()

In [ ]:
import networkx as nx
length=8404
nodes= 9172
G=nx.Graph()
G.add_nodes_from(i for i in range(nodes))
print(G)

Graph with 9172 nodes and 0 edges


In [ ]:
for i in range(nodes):
  G.add_edge(row[i],col[i],weight=weight[i])
print(G)

Graph with 9172 nodes and 4586 edges


In [ ]:
import random
from tqdm import tqdm


def parallel_generate_walks(d_graph: dict, global_walk_length: int, num_walks: int, cpu_num: int,
                            sampling_strategy: dict = None, num_walks_key: str = None, walk_length_key: str = None,
                            neighbors_key: str = None, probabilities_key: str = None, first_travel_key: str = None,
                            quiet: bool = False) -> list:
    """
    Generates the random walks which will be used as the skip-gram input.
    :return: List of walks. Each walk is a list of nodes.
    """

    walks = list()

    if not quiet:
        pbar = tqdm(total=num_walks, desc='Generating walks (CPU: {})'.format(cpu_num))

    for n_walk in range(num_walks):

        # Update progress bar
        if not quiet:
            pbar.update(1)

        # Shuffle the nodes
        shuffled_nodes = list(d_graph.keys())
        random.shuffle(shuffled_nodes)

        # Start a random walk from every node
        for source in shuffled_nodes:
            # Skip nodes with specific num_walks
            if source in sampling_strategy and \
                    num_walks_key in sampling_strategy[source] and \
                    sampling_strategy[source][num_walks_key] <= n_walk:
                continue

            # Start walk
            walk = [source]

            # Calculate walk length
            if source in sampling_strategy:
                walk_length = sampling_strategy[source].get(walk_length_key, global_walk_length)
            else:
                walk_length = global_walk_length
            

            # Perform walk
            while len(walk) < walk_length:

                walk_options = d_graph[walk[-1]].get(neighbors_key, None)

                # Skip dead end nodes
                if not walk_options:
                    break

                if len(walk) == 1:  # For the first step
                    probabilities = d_graph[walk[-1]][first_travel_key]
                    for i in range(10):
                      walk_to = random.choices(walk_options, weights=probabilities)[0]
                      if walk_to>6909:
                        break
                    

                else:
                    probabilities = d_graph[walk[-1]][probabilities_key][walk[-2]]
                    for i in range(10):
                      walk_to = random.choices(walk_options, weights=probabilities)[0]
                      if walk_to>6909:
                        break
                if walk_to<6909:
                  break
                walk.append(walk_to)

            walk = list(map(str, walk))  # Convert all to strings

            walks.append(walk)

    if not quiet:
        pbar.close()

    return walks

In [ ]:
import os
import random
from collections import defaultdict

import gensim
import networkx as nx
import numpy as np
import pkg_resources
from joblib import Parallel, delayed
from tqdm.auto import tqdm



class Node2Vec:
    FIRST_TRAVEL_KEY = 'first_travel_key'
    PROBABILITIES_KEY = 'probabilities'
    NEIGHBORS_KEY = 'neighbors'
    WEIGHT_KEY = 'weight'
    NUM_WALKS_KEY = 'num_walks'
    WALK_LENGTH_KEY = 'walk_length'
    P_KEY = 'p'
    Q_KEY = 'q'

    def __init__(self, graph: nx.Graph, dimensions: int = 128, walk_length: int = 80, num_walks: int = 10, p: float = 1,
                 q: float = 1, weight_key: str = 'weight', workers: int = 1, sampling_strategy: dict = None,
                 quiet: bool = False, temp_folder: str = None, seed: int = None):
        """
        Initiates the Node2Vec object, precomputes walking probabilities and generates the walks.
        :param graph: Input graph
        :param dimensions: Embedding dimensions (default: 128)
        :param walk_length: Number of nodes in each walk (default: 80)
        :param num_walks: Number of walks per node (default: 10)
        :param p: Return hyper parameter (default: 1)
        :param q: Inout parameter (default: 1)
        :param weight_key: On weighted graphs, this is the key for the weight attribute (default: 'weight')
        :param workers: Number of workers for parallel execution (default: 1)
        :param sampling_strategy: Node specific sampling strategies, supports setting node specific 'q', 'p', 'num_walks' and 'walk_length'.
        :param seed: Seed for the random number generator.
        Use these keys exactly. If not set, will use the global ones which were passed on the object initialization
        :param temp_folder: Path to folder with enough space to hold the memory map of self.d_graph (for big graphs); to be passed joblib.Parallel.temp_folder
        """

        self.graph = graph
        self.dimensions = dimensions
        self.walk_length = walk_length
        self.num_walks = num_walks
        self.p = p
        self.q = q
        self.weight_key = weight_key
        self.workers = workers
        self.quiet = quiet
        self.d_graph = defaultdict(dict)

        if sampling_strategy is None:
            self.sampling_strategy = {}
        else:
            self.sampling_strategy = sampling_strategy

        self.temp_folder, self.require = None, None
        if temp_folder:
            if not os.path.isdir(temp_folder):
                raise NotADirectoryError("temp_folder does not exist or is not a directory. ({})".format(temp_folder))

            self.temp_folder = temp_folder
            self.require = "sharedmem"

        if seed is not None:
            random.seed(seed)
            np.random.seed(seed)

        self._precompute_probabilities()
        self.walks = self._generate_walks()

    def _precompute_probabilities(self):
        """
        Precomputes transition probabilities for each node.
        """

        d_graph = self.d_graph

        nodes_generator = self.graph.nodes() if self.quiet \
            else tqdm(self.graph.nodes(), desc='Computing transition probabilities')

        for source in nodes_generator:

            # Init probabilities dict for first travel
            if self.PROBABILITIES_KEY not in d_graph[source]:
                d_graph[source][self.PROBABILITIES_KEY] = dict()

            for current_node in self.graph.neighbors(source):

                # Init probabilities dict
                if self.PROBABILITIES_KEY not in d_graph[current_node]:
                    d_graph[current_node][self.PROBABILITIES_KEY] = dict()

                unnormalized_weights = list()
                d_neighbors = list()

                # Calculate unnormalized weights
                for destination in self.graph.neighbors(current_node):

                    p = self.sampling_strategy[current_node].get(self.P_KEY,
                                                                 self.p) if current_node in self.sampling_strategy else self.p
                    q = self.sampling_strategy[current_node].get(self.Q_KEY,
                                                                 self.q) if current_node in self.sampling_strategy else self.q

                    try:
                        if self.graph[current_node][destination].get(self.weight_key):
                            weight = self.graph[current_node][destination].get(self.weight_key, 1)
                        else: 
                            ## Example : AtlasView({0: {'type': 1, 'weight':0.1}})- when we have edge weight
                            edge = list(self.graph[current_node][destination])[-1]
                            weight = self.graph[current_node][destination][edge].get(self.weight_key, 1)
                            
                    except:
                        weight = 1 
                    
                    if destination == source:  # Backwards probability
                        ss_weight = weight * 1 / p
                    elif destination in self.graph[source]:  # If the neighbor is connected to the source
                        ss_weight = weight
                    else:
                        ss_weight = weight * 1 / q

                    # Assign the unnormalized sampling strategy weight, normalize during random walk
                    unnormalized_weights.append(ss_weight)
                    d_neighbors.append(destination)

                # Normalize
                unnormalized_weights = np.array(unnormalized_weights)
                d_graph[current_node][self.PROBABILITIES_KEY][
                    source] = unnormalized_weights / unnormalized_weights.sum()

            # Calculate first_travel weights for source
            first_travel_weights = []

            for destination in self.graph.neighbors(source):
                first_travel_weights.append(self.graph[source][destination].get(self.weight_key, 1))

            first_travel_weights = np.array(first_travel_weights)
            d_graph[source][self.FIRST_TRAVEL_KEY] = first_travel_weights / first_travel_weights.sum()

            # Save neighbors
            d_graph[source][self.NEIGHBORS_KEY] = list(self.graph.neighbors(source))

    def _generate_walks(self) -> list:
        """
        Generates the random walks which will be used as the skip-gram input.
        :return: List of walks. Each walk is a list of nodes.
        """

        flatten = lambda l: [item for sublist in l for item in sublist]

        # Split num_walks for each worker
        num_walks_lists = np.array_split(range(self.num_walks), self.workers)

        walk_results = Parallel(n_jobs=self.workers, temp_folder=self.temp_folder, require=self.require)(
            delayed(parallel_generate_walks)(self.d_graph,
                                             self.walk_length,
                                             len(num_walks),
                                             idx,
                                             self.sampling_strategy,
                                             self.NUM_WALKS_KEY,
                                             self.WALK_LENGTH_KEY,
                                             self.NEIGHBORS_KEY,
                                             self.PROBABILITIES_KEY,
                                             self.FIRST_TRAVEL_KEY,
                                             self.quiet) for
            idx, num_walks
            in enumerate(num_walks_lists, 1))

        walks = flatten(walk_results)

        return walks

    def fit(self, **skip_gram_params) -> gensim.models.Word2Vec:
        """
        Creates the embeddings using gensim's Word2Vec.
        :param skip_gram_params: Parameters for gensim.models.Word2Vec - do not supply 'size' / 'vector_size' it is
            taken from the Node2Vec 'dimensions' parameter
        :type skip_gram_params: dict
        :return: A gensim word2vec model
        """

        if 'workers' not in skip_gram_params:
            skip_gram_params['workers'] = self.workers

        # Figure out gensim version, naming of output dimensions changed from size to vector_size in v4.0.0
        gensim_version = pkg_resources.get_distribution("gensim").version
        size = 'size' if gensim_version < '4.0.0' else 'vector_size'
        if size not in skip_gram_params:
            skip_gram_params[size] = self.dimensions

        if 'sg' not in skip_gram_params:
            skip_gram_params['sg'] = 1

        return gensim.models.Word2Vec(self.walks, **skip_gram_params)

In [ ]:
mdl=Node2Vec(G)


Computing transition probabilities:   0%|          | 0/9172 [00:00<?, ?it/s]

Generating walks (CPU: 1):   0%|          | 0/10 [00:00<?, ?it/s]

In [ ]:
m=mdl.fit(window=10,min_count=4,batch_words=4)
print(m)

Word2Vec(vocab=9172, size=128, alpha=0.025)


In [ ]:
import pandas as pd
emb_df=(pd.DataFrame(
    [m.wv.get_vector(str(n)) for n in G.nodes()],
    index=G.nodes
))
print(emb_df)

           0         1         2         3         4         5         6    \
0     0.002923 -0.002659 -0.002063  0.000612 -0.001008 -0.003750 -0.002614   
1     0.003285  0.000550  0.000537 -0.000129 -0.001163 -0.003704 -0.000612   
2     0.001755  0.000459  0.002709  0.000521  0.003775  0.003477  0.001175   
3    -0.001597  0.002907 -0.000938 -0.000410 -0.001842  0.002124 -0.003581   
4    -0.000621 -0.002040  0.002296  0.002044 -0.000704  0.000663 -0.002717   
...        ...       ...       ...       ...       ...       ...       ...   
9167  0.003223 -0.003048 -0.003713 -0.002737  0.003413  0.002091  0.001443   
9168  0.001284 -0.001075  0.003162  0.001371  0.002795 -0.002957 -0.000344   
9169  0.000455 -0.001956  0.000798 -0.003897 -0.001806 -0.001363  0.001917   
9170  0.488498  0.371411 -0.716274 -0.192225  0.078682  0.348332  0.101450   
9171  0.590596  0.126126 -0.672912 -0.345784  0.076542  0.667026  0.070526   

           7         8         9    ...       118       119    

In [ ]:
weighted_node_embeddings=emb_df.to_numpy()
embeddings=weighted_node_embeddings[0:6908]
print(embeddings.shape)

(6908, 128)


In [ ]:
from sklearn.manifold import TSNE
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import accuracy_score
from sklearn.metrics.pairwise import pairwise_distances
from sklearn import preprocessing

import numpy as np

In [ ]:
print(label_list)

[['0.0', '0.0', '0.667', '0.0'], ['0.0', '0.0', '0.5', '0.0'], ['0.32', '0.0', '0.0', '0.0'], ['0.0', '0.0', '0.0', '0.8540000000000001'], ['0.271', '0.0', '0.0', '0.0'], ['0.0', '0.0', '0.0', '0.312'], ['0.0', '0.292', '0.0', '0.0'], ['0.48', '0.0', '0.0', '0.0'], ['0.312', '0.0', '0.0', '0.0'], ['0.22899999999999998', '0.0', '0.0', '0.0'], ['0.0', '0.354', '0.0', '0.0'], ['0.688', '0.0', '0.0', '0.0'], ['0.0', '0.75', '0.0', '0.0'], ['0.0', '0.0', '0.0', '0.562'], ['0.0', '0.0', '0.708', '0.0'], ['0.0', '0.0', '0.0', '0.46'], ['0.0', '0.0', '0.0', '0.292'], ['0.0', '0.0', '0.494', '0.0'], ['0.0', '0.0', '0.491', '0.0'], ['0.0', '0.0', '0.0', '0.521'], ['0.0', '0.0', '0.312', '0.0'], ['0.0', '0.235', '0.0', '0.0'], ['0.0', '0.0', '0.0', '0.583'], ['0.0', '0.0', '0.562', '0.0'], ['0.0', '0.0', '0.479', '0.0'], ['0.688', '0.0', '0.0', '0.0'], ['0.708', '0.0', '0.0', '0.0'], ['0.82', '0.0', '0.0', '0.0'], ['0.0', '0.44', '0.0', '0.0'], ['0.0', '0.0', '0.0', '0.542'], ['0.0', '0.332999999

In [ ]:
new_label_list=[]
for i in range(train_size):
    index=0
    max=-1
    doc_meta = shuffle_doc_name_list[i]
    temp = doc_meta.split('\t')
    label = temp[2:6]
    print(label)
    if label[0]=='joy':
      continue
    for j in range(len(label)):
      if float(label[j]) > max:
        max = float(label[j])
        index = j
    new_label_list.append(index+1)
    print("-->",index)
print(len(new_label_list))

In [ ]:
X = embeddings

In [ ]:
# y holds the corresponding target values
y=np.array(new_label_list)
X_train, X_test, y_train, y_test = train_test_split(
    X, y, train_size=0.75, test_size=None, random_state=42
)
print(
    "Array shapes:\n X_train = {}\n y_train = {}\n X_test = {}\n y_test = {}".format(
        X_train.shape, y_train.shape, X_test.shape, y_test.shape
    )
)

Array shapes:
 X_train = (5181, 128)
 y_train = (5181,)
 X_test = (1727, 128)
 y_test = (1727,)


In [ ]:
print(y_train)

[3 1 1 ... 2 4 4]


In [ ]:
print(X)

[[ 0.00292282 -0.0026592  -0.0020627  ... -0.00160413 -0.00354387
  -0.00039904]
 [ 0.00328548  0.00054959  0.00053657 ...  0.00267006  0.00363886
   0.00101346]
 [ 0.00175531  0.00045899  0.00270897 ... -0.00218832  0.00061671
   0.00224919]
 ...
 [ 0.00320742 -0.00227584  0.00080628 ... -0.00357866 -0.00117836
  -0.00051896]
 [ 0.00063347 -0.00215442  0.00274018 ...  0.00087872 -0.00363079
  -0.0032172 ]
 [ 0.00239224 -0.00119189 -0.00174019 ... -0.00136131  0.00220116
  -0.00273196]]


In [ ]:
clf = LogisticRegression(
    penalty='l2',
    max_iter=100000,
)
clf.fit(X_train, y_train)

LogisticRegression(max_iter=100000)

In [ ]:
y_pred = clf.predict(X_test)

In [ ]:
y_test

array([4, 3, 4, ..., 4, 3, 4])

In [ ]:
y_pred

array([4, 4, 4, ..., 4, 4, 4])

In [ ]:
print("Accuracy of LinearRegression is ",accuracy_score(y_test, y_pred))

Accuracy of LinearRegression is  0.31036479444122755


In [ ]:
from sklearn.metrics import fbeta_score
print("Accuracy of F score is ",fbeta_score(y_test, y_pred, pos_label=1,beta=0.5,average='micro'))

Accuracy of F score is  0.31036479444122755


In [ ]:
from sklearn.svm import SVR
svr = SVR(kernel = 'linear',C = 1000)
svr.fit(X_train,y_train)
y_test_pred = svr.predict(X_test)
y_train_pred = svr.predict(X_train)

In [ ]:
y_test_pr=np.round(y_test_pred,0)

y_test_p=np.int_(y_test_pr)
print(y_test_p)

[3 3 3 ... 3 3 2]


In [ ]:
print("Accuracy through SVM is ",accuracy_score(y_test, y_test_p))


Accuracy through SVM is  0.22756224667052694


In [ ]:
from sklearn.metrics import fbeta_score
print("F Score through SVM is ", fbeta_score(y_test, y_test_p, pos_label=1,beta=0.5,average='micro'))

F Score through SVM is  0.22756224667052694


In [ ]:
from sklearn.naive_bayes import GaussianNB
gnb = GaussianNB()
gnb.fit(X_train, y_train)
  
# making predictions on the testing set
y_pred = gnb.predict(X_test)
  
# comparing actual response values (y_test) with predicted response values (y_pred)
from sklearn import metrics
print("Gaussian Naive Bayes model accuracy(in %):", metrics.accuracy_score(y_test, y_pred)*100)
print(fbeta_score(y_test, y_pred, pos_label=1,beta=0.5,average='micro'))

Gaussian Naive Bayes model accuracy(in %): 28.720324261725537
0.2872032426172554


In [ ]:
from mlxtend.plotting import plot_decision_regions
from sklearn.metrics import accuracy_score
from sklearn.ensemble import RandomForestClassifier

forest = RandomForestClassifier(criterion='gini',
                                 n_estimators=5,
                                 random_state=1,
                                 n_jobs=2)
#
# Fit the model
#
forest.fit(X_train, y_train)
#
# Measure model performance
#
y_pred = forest.predict(X_test)
print('Accuracy: %.3f' % accuracy_score(y_test, y_pred))
print(fbeta_score(y_test, y_pred, pos_label=1,beta=0.5,average='micro'))

Accuracy: 0.237
0.2368268674001158
